# Cross-Sections

This section demonstrates how to extract both horizontal and vertical cross-sections from an unstructured grid using UXarray, which allows the analysis and visualization across slices of grids. Cross-sections can be performed directly on a `ux.Grid` object or on a `ux.UxDataArray`.

## Horizontal Cross-Sections

Horizontal cross-sections extract slices at constant latitudes or longitudes on the horizontal plane.


In [1]:
import cartopy.crs as ccrs
import geoviews as gv
import geoviews.feature as gf

import uxarray as ux

projection = ccrs.Robinson()

In [2]:
base_path = "../../test/meshfiles/ugrid/outCSne30/"
grid_path = base_path + "outCSne30.ug"
data_path = base_path + "outCSne30_vortex.nc"

uxds = ux.open_dataset(grid_path, data_path)
uxds["psi"].plot(
    cmap="inferno",
    periodic_elements="split",
    projection=projection,
    title="Global Plot",
)

:Image   [Longitude,Latitude]   (Longitude_Latitude psi)

### Constant Latitude

Horizontal cross-sections along constant latitude lines can be obtained by using the  ``.cross_section.constant_latitude(lat)`` method. The sliced grid will be made up of the faces that contain at least one edge that intersects with a line of constant latitude.


For example, we can obtain a cross-section at 0 degrees latitude by doing the following:

In [3]:
lat = 0

uxda_constant_lat = uxds["psi"].cross_section.constant_latitude(lat)

OMP: Info #276: omp_set_nested routine deprecated, please use omp_set_max_active_levels instead.


Since the result is a new ``UxDataArray``, we can directly plot the result to see the cross-section.

In [4]:
(
    uxda_constant_lat.plot(
        rasterize=False,
        backend="bokeh",
        cmap="inferno",
        projection=projection,
        global_extent=True,
        coastline=True,
        title=f"Cross Section at {lat} degrees latitude",
    )
    * gf.grid(projection=projection)
)

:Overlay
   .Polygons.I  :Polygons   [Longitude,Latitude]   (psi)
   .Coastline.I :Feature   [Longitude,Latitude]
   .Grid.I      :Feature   [Longitude,Latitude]

You can also perform operations on the cross-section, such as taking the mean.

In [5]:
print(f"Global Mean: {uxds['psi'].data.mean()}")
print(f"Mean at {lat} degrees lat: {uxda_constant_lat.data.mean()}")

Global Mean: 1.0000000015332655
Mean at 0 degrees lat: 1.0000000052455802


### Constant Longitude


Horizontal cross-sections along constant longitude lines can be obtained using the ``.cross_section.constant_longitude(lon)`` method. The sliced grid will be made up of the faces that contain at least one edge that intersects with a line of constant longitude.


In [6]:
lon = 90

uxda_constant_lon = uxds["psi"].cross_section.constant_longitude(lon)

In [7]:
(
    uxda_constant_lon.plot(
        rasterize=False,
        backend="bokeh",
        cmap="inferno",
        projection=projection,
        global_extent=True,
        coastline=True,
        title=f"Cross Section at {lon} degrees longitude",
        periodic_elements="split",
    )
    * gf.grid(projection=projection)
)

:Overlay
   .Polygons.I  :Polygons   [Longitude,Latitude]   (psi)
   .Coastline.I :Feature   [Longitude,Latitude]
   .Grid.I      :Feature   [Longitude,Latitude]

### Constant Latitude Interval

Horizontal cross-sections between two lines of latitudes can be obtained using the ``.cross_section.constant_latitude_interval(lats)`` method. The sliced grid will contain faces that are strictly between the latitude interval.

In [8]:
lats = [-20, 20]

uxda_constant_lat_interval = uxds["psi"].cross_section.constant_latitude_interval(lats)

In [9]:
(
    uxda_constant_lat_interval.plot(
        rasterize=False,
        backend="bokeh",
        cmap="inferno",
        projection=projection,
        global_extent=True,
        coastline=True,
        title=f"Cross Section between {lats[0]} and {lats[1]} degrees latitude",
        periodic_elements="split",
    )
    * gf.grid(projection=projection)
)

:Overlay
   .Polygons.I  :Polygons   [Longitude,Latitude]   (psi)
   .Coastline.I :Feature   [Longitude,Latitude]
   .Grid.I      :Feature   [Longitude,Latitude]

### Constant Longitude Interval

Horizontal cross-sections between two lines of longitude can be obtained using the ``.cross_section.constant_longitude_interval(lons)`` method. The sliced grid will contain faces that are strictly between the longitude interval.


In [10]:
lons = [-25, 25]

uxda_constant_lon_interval = uxds["psi"].cross_section.constant_longitude_interval(lons)

In [11]:
(
    uxda_constant_lon_interval.plot(
        rasterize=False,
        backend="bokeh",
        cmap="inferno",
        projection=projection,
        global_extent=True,
        coastline=True,
        title=f"Cross Section between {lons[0]} and {lons[1]} degrees longitude",
        periodic_elements="split",
    )
    * gf.grid(projection=projection)
)

:Overlay
   .Polygons.I  :Polygons   [Longitude,Latitude]   (psi)
   .Coastline.I :Feature   [Longitude,Latitude]
   .Grid.I      :Feature   [Longitude,Latitude]

## Vertical Cross-Sections

Vertical cross-sections work on 3D data (with vertical levels like atmospheric pressure levels, ocean depths, etc.) and extract slices along constant latitudes or longitudes while preserving ALL vertical levels. This creates a 2D vertical transect showing how data varies spatially and vertically.

### Vertical Constant Latitude

Vertical cross-sections along constant latitude lines (zonal transects) can be obtained using the ``.cross_section.vertical_constant_latitude(lat, vertical_coord)`` method. This takes a horizontal slice at the specified latitude across ALL vertical levels, creating a longitude vs depth/height transect.


In [12]:
import numpy as np

# Create 3D data with vertical dimension for demonstration
depth_levels = np.array([0, 10, 20, 30, 40])
psi_3d = uxds["psi"].expand_dims(depth=depth_levels)

# Extract vertical cross-section at constant latitude
lat = 0
vertical_lat_section = psi_3d.cross_section.vertical_constant_latitude(
    lat=lat, vertical_coord="depth"
)

print(f"Original 2D data shape: {uxds['psi'].shape}")
print(f"3D data shape: {psi_3d.shape}")
print(f"Vertical cross-section shape: {vertical_lat_section.shape}")

Original 2D data shape: (5400,)
3D data shape: (5, 5400)
Vertical cross-section shape: (5, 240)


### Vertical Constant Longitude

Vertical cross-sections along constant longitude lines (meridional transects) can be obtained using the ``.cross_section.vertical_constant_longitude(lon, vertical_coord)`` method. This takes a horizontal slice at the specified longitude across ALL vertical levels, creating a latitude vs depth/height transect.


In [13]:
# Extract vertical cross-section at constant longitude
lon = 90
vertical_lon_section = psi_3d.cross_section.vertical_constant_longitude(
    lon=lon, vertical_coord="depth"
)

print(f"Vertical longitude cross-section shape: {vertical_lon_section.shape}")

Vertical longitude cross-section shape: (5, 120)


**Key Points about Vertical Cross-Sections:**
- Require 3D data with a vertical coordinate dimension (e.g., pressure levels, depth, height)
- The `vertical_coord` parameter must specify which dimension represents the vertical axis
- Result preserves all vertical levels, creating a 2D transect (horizontal_faces × vertical_levels)
- Can be visualized as contour plots or heatmaps showing spatial-vertical structure
